In [2]:
import os
import os.path
from collections import Counter

In [42]:
#input
blast_db = "/mnt/data/ncbi/blast/db/nt"
scaffold = "/home/dzilov/scripts/contera/test_data/scaffolds.fasta"
threads = 100

blastn_taxid_out = "/home/dzilov/scripts/contera/results/Ecoli19.outfmt6"
output = "/home/dzilov/scripts/contera/results/"
scaforarg = scaffold.split("/")[-1].split(".")[0]
prefix = blastn_taxid_out.split("/")[-1].split(".")[0]

scaffolds_filtered = output + scaforarg + "_filtered.fasta"
contera_report = output + prefix + ".contera_report.txt"
vectors_log = output + prefix + ".vectors.tsv"
phages_log = output + prefix + ".phages.tsv"
adapters_report = output + prefix + ".adapters_report.outfmt6"

In [43]:
#нужно получить из бласта:
# 1) Процентное отношение бактерий в сборке (каунтер по sscinames)
# 2) Три самых часто встречающихся айди таксона (каунтер по staxids)
# 3) Части контигов, которые нужно удалить (от qstart до qend в контиге qseqid)

In [110]:
# Закинуть в правило BLAST

command = """blastn \
-db nt \
-query %s \
-evalue 0.00001 \
-outfmt '6 qseqid sseqid pident qstart qend length evalue sscinames staxids' \
-max_target_seqs 5 \
-num_threads %s \
-out %s""" % (scaffold, threads, blastn_taxid_out)

print(command)
#os.system(command)

blastn -db nt -query /home/dzilov/scripts/contera/test_data/scaffolds.fasta -evalue 0.00001 -outfmt '6 qseqid sseqid pident qstart qend length evalue sscinames staxids' -max_target_seqs 5 -num_threads 100 -out /home/dzilov/scripts/contera/results/Ecoli19.outfmt6


In [111]:
bact_taxid = {}
contigs = {}

vectors = []
phages = []

bact_length = Counter()
taxid_length = Counter()
total_length = 0

bact_seq = {}
with open(blastn_taxid_out) as fh:
    for line in fh:
        line = line.strip().split("\t")
        #Column names
        contig = line[0]
        contigs[contig] = []
        ident = float(line[2])
        start = line[3]
        end = line[4]
        length = int(line[5])
        bact_full_name = line[7]
        bacteria = " ".join(line[7].split(" ")[:2])
        taxid = line[8]
        
        if "vector" in bact_full_name or "Vector" in bact_full_name:
            vectors.append(line)
        if "phage" in bact_full_name or "Phage" in bact_full_name:
            phages.append(line)
        
        bact_length[bacteria] += length
        taxid_length[taxid] += length
        total_length += length
        
        bact_seq[bacteria] = contig + ":" + start + ".." + end

['NODE_1_length_344957_cov_96.369759', 'gi|1609454293|gb|CP038505.1|', '99.973', '859', '182709', '181860', '0.0', 'Escherichia coli', '562']
['NODE_1_length_344957_cov_96.369759', 'gi|1609454293|gb|CP038505.1|', '99.995', '185883', '344951', '159069', '0.0', 'Escherichia coli', '562']
['NODE_1_length_344957_cov_96.369759', 'gi|1609454293|gb|CP038505.1|', '99.968', '182810', '185903', '3094', '0.0', 'Escherichia coli', '562']
['NODE_1_length_344957_cov_96.369759', 'gi|1609454293|gb|CP038505.1|', '97.778', '2609', '3733', '1125', '0.0', 'Escherichia coli', '562']
['NODE_1_length_344957_cov_96.369759', 'gi|1609454293|gb|CP038505.1|', '95.843', '1', '866', '866', '0.0', 'Escherichia coli', '562']
['NODE_1_length_344957_cov_96.369759', 'gi|1609454293|gb|CP038505.1|', '95.833', '1', '864', '864', '0.0', 'Escherichia coli', '562']
['NODE_1_length_344957_cov_96.369759', 'gi|1609454293|gb|CP038505.1|', '95.481', '1', '863', '863', '0.0', 'Escherichia coli', '562']
['NODE_1_length_344957_cov_96

['NODE_31_length_54578_cov_104.363666', 'gi|1672815629|gb|CP040390.1|', '81.572', '21023', '21387', '369', '2.63e-73', 'Escherichia coli', '562']
['NODE_31_length_54578_cov_104.363666', 'gi|1672815629|gb|CP040390.1|', '98.611', '12317', '12460', '144', '1.24e-61', 'Escherichia coli', '562']
['NODE_31_length_54578_cov_104.363666', 'gi|1672815629|gb|CP040390.1|', '98.519', '1', '135', '135', '1.25e-56', 'Escherichia coli', '562']
['NODE_31_length_54578_cov_104.363666', 'gi|1672815629|gb|CP040390.1|', '86.822', '45518', '45643', '129', '1.30e-26', 'Escherichia coli', '562']
['NODE_31_length_54578_cov_104.363666', 'gi|1672815629|gb|CP040390.1|', '86.441', '45528', '45643', '118', '1.01e-22', 'Escherichia coli', '562']
['NODE_31_length_54578_cov_104.363666', 'gi|1672815629|gb|CP040390.1|', '81.746', '605', '729', '126', '4.75e-16', 'Escherichia coli', '562']
['NODE_31_length_54578_cov_104.363666', 'gi|1672815629|gb|CP040390.1|', '100.000', '12168', '12216', '49', '3.70e-12', 'Escherichia co

['NODE_131_length_704_cov_251.991334', 'gi|1752751047|gb|CP044191.1|', '99.574', '1', '704', '704', '0.0', 'Shigella sonnei', '624']
['NODE_131_length_704_cov_251.991334', 'gi|1752751047|gb|CP044191.1|', '99.574', '1', '704', '704', '0.0', 'Shigella sonnei', '624']
['NODE_131_length_704_cov_251.991334', 'gi|1752751047|gb|CP044191.1|', '99.574', '1', '704', '704', '0.0', 'Shigella sonnei', '624']
['NODE_131_length_704_cov_251.991334', 'gi|1752751047|gb|CP044191.1|', '99.574', '1', '704', '704', '0.0', 'Shigella sonnei', '624']
['NODE_131_length_704_cov_251.991334', 'gi|1752751047|gb|CP044191.1|', '99.574', '1', '704', '704', '0.0', 'Shigella sonnei', '624']
['NODE_131_length_704_cov_251.991334', 'gi|1752751047|gb|CP044191.1|', '99.574', '1', '704', '704', '0.0', 'Shigella sonnei', '624']
['NODE_131_length_704_cov_251.991334', 'gi|1752751047|gb|CP044191.1|', '99.574', '1', '704', '704', '0.0', 'Shigella sonnei', '624']
['NODE_131_length_704_cov_251.991334', 'gi|1752751047|gb|CP044191.1|'

In [112]:
len(contigs)

176

In [113]:
target_bact_seq = {}
bact_perc = Counter()
for bact, length in bact_length.most_common():
    bact_perc[bact] = length/total_length * 100
    
print("Bacterial content is:", bact_perc.most_common(5))
print("Most common taxon ID is:", taxid_length.most_common(5))

Bacterial content is: [('Escherichia coli', 98.64001261692864), ('Salmonella enterica', 0.4629528003266352), ('Shigella sonnei', 0.31416017217919956), ('uncultured bacterium', 0.16100092499377766), ('Shigella boydii', 0.10910131062736461)]
Most common taxon ID is: [('562', 28597003), ('696406', 209852), ('624', 93026), ('59201', 88522), ('216592', 81464)]


In [114]:
target_bact_sciname = bact_perc.most_common(1)[0][0]
print(target_bact_sciname)

Escherichia coli


In [149]:
contigs

{'NODE_1_length_344957_cov_96.369759': [],
 'NODE_2_length_325942_cov_102.762117': [],
 'NODE_3_length_287729_cov_94.031467': [],
 'NODE_4_length_250910_cov_98.009044': [],
 'NODE_5_length_244486_cov_93.153823': [],
 'NODE_6_length_215299_cov_95.459028': [],
 'NODE_7_length_197492_cov_103.387060': [],
 'NODE_8_length_166137_cov_94.879893': [],
 'NODE_9_length_150365_cov_103.818634': [],
 'NODE_10_length_145674_cov_102.920837': [],
 'NODE_11_length_143899_cov_91.697500': [],
 'NODE_12_length_123243_cov_95.558238': [],
 'NODE_13_length_120942_cov_98.958325': [],
 'NODE_14_length_118631_cov_98.430568': [],
 'NODE_15_length_114688_cov_100.564590': [],
 'NODE_16_length_113743_cov_100.053276': [],
 'NODE_17_length_94719_cov_102.993752': [],
 'NODE_18_length_93611_cov_100.780658': [],
 'NODE_19_length_92542_cov_102.878883': [],
 'NODE_20_length_92411_cov_109.631420': [],
 'NODE_21_length_92210_cov_96.314010': [],
 'NODE_22_length_88007_cov_99.650523': [],
 'NODE_23_length_86740_cov_103.633346

In [148]:
parts_to_delete = {} #dictionary where key is node, value is list of contaminated parts of node
i = 0
tot_len =0
for node, position in contigs.items():
    with open(blastn_taxid_out) as fh:
        for line in fh:
            line = line.strip().split("\t")
            
            #column names
            contig = line[0]
            ident = float(line[2])
            start = line[3]
            end = line[4]
            bacteria = " ".join(line[7].split(" ")[:2])

            if contig == node and bacteria != target_bact_sciname:
                if start + ":" + end in position:
                    continue
                else:
                    position.append(start + ":" + end)
                break
        fh.close()

In [124]:
i

268

In [165]:
#looking for most long sequences to delete
delete_seq = {}

for node, position in contigs.items():
    if position:
        position.sort(key=lambda x : (int(x.split(":")[0]), -1 * int(x.split(":")[1])))
        print(position)
        delete_seq[node] = []
        
        i = 1
        ps,pe = map(int, position[0].split(":"))
        while i < len(position):
            s,e = map(int, position[i].split(":"))
            if pe + 1 < s:
                delete_seq[node].append((ps, pe))
                ps, pe = s, e
                i += 1
                continue
            
            pe = max(e, pe)
            i += 1
        delete_seq[node].append((ps, pe))
        
#         for i in range(1, len(position)):
#             ps,pe = map(int, position[i-1].split(":"))
            
#             if ps <= s and e <= pe:
#                 delete_seq[node].append((ps, pe))
#             elif ps <= s and pe <= e:
#                 delete_seq[node].append((ps, e))
        print(delete_seq[node])

['1:1917', '1909:4987', '5109:5211', '6450:8821', '8822:77701', '65092:65423', '68486:68816', '68490:68985', '69675:70027', '74832:75328', '76620:76972', '80247:83879']
[(1, 4987), (5109, 5211), (6450, 77701), (80247, 83879)]
['1:162', '11486:11736', '15254:16492', '15254:16048', '15317:15480', '15504:15558', '15507:15561', '16040:26204', '16488:26231', '26188:28144', '26215:28144', '28194:28352', '28197:28352', '29097:29824', '30035:36433', '36430:51308', '51384:54829', '53080:53134', '54379:54829', '54391:54829', '54913:55540', '55535:57156', '57643:57865', '57646:57865', '57647:57865']
[(1, 162), (11486, 11736), (15254, 28144), (28194, 28352), (29097, 29824), (30035, 51308), (51384, 54829), (54913, 57156), (57643, 57865)]
['1:25898', '14757:14857', '14845:14945', '14907:14946', '19363:19550', '19363:19454', '19394:19550', '19460:19646', '19463:19591', '19512:19590', '19514:19563', '19541:19647', '19556:19646', '19556:19594', '28289:30824', '32326:33347']
[(1, 25898), (28289, 30824),

In [155]:
delete_seq

{'NODE_24_length_83879_cov_151.567616': ['1:1917',
  '1909:4987',
  '5109:5211',
  '6450:8821',
  '8822:77701',
  '65092:65423',
  '68486:68816',
  '68490:68985',
  '69675:70027',
  '74832:75328',
  '76620:76972',
  '80247:83879'],
 'NODE_28_length_57865_cov_145.685181': ['1:162',
  '11486:11736',
  '15254:16048',
  '15254:16492',
  '15317:15480',
  '15504:15558',
  '15507:15561',
  '16040:26204',
  '16488:26231',
  '26188:28144',
  '26215:28144',
  '28194:28352',
  '28197:28352',
  '29097:29824',
  '30035:36433',
  '36430:51308',
  '51384:54829',
  '53080:53134',
  '54379:54829',
  '54391:54829',
  '54913:55540',
  '55535:57156',
  '57643:57865',
  '57646:57865',
  '57647:57865'],
 'NODE_42_length_33347_cov_94.659211': ['1:25898',
  '14757:14857',
  '14845:14945',
  '14907:14946',
  '19363:19454',
  '19363:19550',
  '19394:19550',
  '19460:19646',
  '19463:19591',
  '19512:19590',
  '19514:19563',
  '19541:19647',
  '19556:19594',
  '19556:19646',
  '28289:30824',
  '32326:33347'],
 '

In [20]:
taxid_list = []
for i in taxid_length.most_common(50):
    taxid = int(i[0])
    taxid_list.append(taxid)
print(taxid_list[:10])

[562, 83334, 1045010, 2605619, 624, 622, 83333, 623, 573, 1038927]


blastn -db nt -query /home/dzilov/prokaryotic_pipeline/data/ecoli19/unicycler/assembly.fasta -evalue 0.000001 -outfmt '6 qseqid sseqid pident qstart qend length evalue sscinames staxids' -num_threads 50 -out /home/dzilov/prokaryotic_pipeline/data/ecoli19/blast/unicycler/Ecolli19-2_S2_L001.blast_report.tsv


{23: []}
{23: ['pop']}


In [17]:
bact_report = []
for taxon, size in count_names.most_common(100):
    bact_report.append(taxon + " " + "%s%%" % round(100.*size/total_length, 2))
print("\n", bact_report, "\n")


 [] 



In [25]:
bacteria_id = []
for i in count_id.most_common()[:3]:
    bacteria_id.append(str(i[0]) + " = " + str(i[1]/total_length * 100) + "%")
print("THE MOST COMMON ID IS : " + ", ".join(bacteria_id))

THE MOST COMMON ID IS : 


In [26]:
from collections import Counter
count_names = Counter()
count_id = Counter()
total_length = 0
not_bacteria_node = []
unnown_id = []
with open(contera_log, "w") as fw:
    fw.write("UNNOWN ID'S: \n")
    for key, value in cont_to_blast.items():
        length = cont_to_len[key]
        val_split = value.split('.')[0]
        taxon_id = refids.find_one({"accession":val_split})
        print(taxon_id)
        if taxon_id == None:
            fw.write(key + " : " + val_split + "\n")
        else:
            taxon_id = taxon_id["taxid"]
            taxon_name = taxids.find_one({"_id":taxon_id})["name"]
            taxon_name = " ".join(taxon_name.split()[:2])
            count_names[taxon_name] += length
            count_id[taxon_id] += length
            total_length += length
            if taxon_name != count_names.most_common()[0][0]:
                not_bacteria_node.append(key)
                
print(not_bacteria_node)

None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None


In [10]:
bact_taxid = {}
with open(blastn_taxid_out) as fh:
    for line in fh:
        line = line.strip().split("\t")
        bacteria = " ".join(line[7].split(" ")[:2])
        if bacteria != "Escherichia coli":
            print(line)

['1', 'gi|1707092254|gb|CP041620.1|', '0.0', '78528', '1707092254', 'CP041620', '623', 'Shigella flexneri', 'Shigella flexneri', 'Shigella flexneri strain C32 chromosome, complete genome']
['1', 'gi|1707092254|gb|CP041620.1|', '0.0', '72982', '1707092254', 'CP041620', '623', 'Shigella flexneri', 'Shigella flexneri', 'Shigella flexneri strain C32 chromosome, complete genome']
['1', 'gi|1707092254|gb|CP041620.1|', '0.0', '47437', '1707092254', 'CP041620', '623', 'Shigella flexneri', 'Shigella flexneri', 'Shigella flexneri strain C32 chromosome, complete genome']
['1', 'gi|1707092254|gb|CP041620.1|', '0.0', '41877', '1707092254', 'CP041620', '623', 'Shigella flexneri', 'Shigella flexneri', 'Shigella flexneri strain C32 chromosome, complete genome']
['1', 'gi|1707092254|gb|CP041620.1|', '0.0', '31272', '1707092254', 'CP041620', '623', 'Shigella flexneri', 'Shigella flexneri', 'Shigella flexneri strain C32 chromosome, complete genome']
['1', 'gi|1707092254|gb|CP041620.1|', '0.0', '29595', '

['7', 'gi|1707092254|gb|CP041620.1|', '0.0', '82031', '1707092254', 'CP041620', '623', 'Shigella flexneri', 'Shigella flexneri', 'Shigella flexneri strain C32 chromosome, complete genome']
['7', 'gi|1707092254|gb|CP041620.1|', '0.0', '55502', '1707092254', 'CP041620', '623', 'Shigella flexneri', 'Shigella flexneri', 'Shigella flexneri strain C32 chromosome, complete genome']
['7', 'gi|1707092254|gb|CP041620.1|', '0.0', '39709', '1707092254', 'CP041620', '623', 'Shigella flexneri', 'Shigella flexneri', 'Shigella flexneri strain C32 chromosome, complete genome']
['7', 'gi|1707092254|gb|CP041620.1|', '0.0', '32723', '1707092254', 'CP041620', '623', 'Shigella flexneri', 'Shigella flexneri', 'Shigella flexneri strain C32 chromosome, complete genome']
['7', 'gi|1707092254|gb|CP041620.1|', '0.0', '30768', '1707092254', 'CP041620', '623', 'Shigella flexneri', 'Shigella flexneri', 'Shigella flexneri strain C32 chromosome, complete genome']
['7', 'gi|1707092254|gb|CP041620.1|', '0.0', '17898', '

['10', 'gi|1347826641|gb|CP026875.1|', '1.45e-99', '383', '1347826641', 'CP026875', '621', 'Shigella boydii', 'Shigella boydii', 'Shigella boydii strain NCTC 9734 chromosome']
['10', 'gi|1347826641|gb|CP026875.1|', '1.50e-74', '300', '1347826641', 'CP026875', '621', 'Shigella boydii', 'Shigella boydii', 'Shigella boydii strain NCTC 9734 chromosome']
['10', 'gi|1347826641|gb|CP026875.1|', '1.22e-40', '187', '1347826641', 'CP026875', '621', 'Shigella boydii', 'Shigella boydii', 'Shigella boydii strain NCTC 9734 chromosome']
['10', 'gi|1347826641|gb|CP026875.1|', '1.23e-35', '171', '1347826641', 'CP026875', '621', 'Shigella boydii', 'Shigella boydii', 'Shigella boydii strain NCTC 9734 chromosome']
['10', 'gi|1347826641|gb|CP026875.1|', '4.45e-30', '152', '1347826641', 'CP026875', '621', 'Shigella boydii', 'Shigella boydii', 'Shigella boydii strain NCTC 9734 chromosome']
['10', 'gi|1347826641|gb|CP026875.1|', '9.91e-07', '75.0', '1347826641', 'CP026875', '621', 'Shigella boydii', 'Shigella

['14', 'gi|1002749888|gb|CP012137.1|', '1.33e-14', '100', '1002749888', 'CP012137', '42897', 'Shigella flexneri 2a', 'Shigella flexneri 2a', 'Shigella flexneri 2a strain 981, complete genome']
['14', 'gi|1002749888|gb|CP012137.1|', '4.80e-14', '99.0', '1002749888', 'CP012137', '42897', 'Shigella flexneri 2a', 'Shigella flexneri 2a', 'Shigella flexneri 2a strain 981, complete genome']
['14', 'gi|1002749888|gb|CP012137.1|', '8.02e-12', '91.6', '1002749888', 'CP012137', '42897', 'Shigella flexneri 2a', 'Shigella flexneri 2a', 'Shigella flexneri 2a strain 981, complete genome']
['14', 'gi|1002749888|gb|CP012137.1|', '8.02e-12', '91.6', '1002749888', 'CP012137', '42897', 'Shigella flexneri 2a', 'Shigella flexneri 2a', 'Shigella flexneri 2a strain 981, complete genome']
['14', 'gi|1002749888|gb|CP012137.1|', '2.89e-11', '89.8', '1002749888', 'CP012137', '42897', 'Shigella flexneri 2a', 'Shigella flexneri 2a', 'Shigella flexneri 2a strain 981, complete genome']
['14', 'gi|1002749888|gb|CP0121

['19', 'gi|1752751047|gb|CP044191.1|', '0.018', '60.2', '1752751047', 'CP044191', '624', 'Shigella sonnei', 'Shigella sonnei', 'Shigella sonnei strain AR-0422 chromosome']
['19', 'gi|1752751047|gb|CP044191.1|', '0.018', '60.2', '1752751047', 'CP044191', '624', 'Shigella sonnei', 'Shigella sonnei', 'Shigella sonnei strain AR-0422 chromosome']
['19', 'gi|1752751047|gb|CP044191.1|', '0.018', '60.2', '1752751047', 'CP044191', '624', 'Shigella sonnei', 'Shigella sonnei', 'Shigella sonnei strain AR-0422 chromosome']
['19', 'gi|1752751047|gb|CP044191.1|', '0.018', '60.2', '1752751047', 'CP044191', '624', 'Shigella sonnei', 'Shigella sonnei', 'Shigella sonnei strain AR-0422 chromosome']
['19', 'gi|1752751047|gb|CP044191.1|', '0.018', '60.2', '1752751047', 'CP044191', '624', 'Shigella sonnei', 'Shigella sonnei', 'Shigella sonnei strain AR-0422 chromosome']
['19', 'gi|1752751047|gb|CP044191.1|', '0.018', '60.2', '1752751047', 'CP044191', '624', 'Shigella sonnei', 'Shigella sonnei', 'Shigella son

...

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



['70', 'gi|1348323427|gb|CP014099.2|', '7.05e-31', '150', '1348323427', 'CP014099', '624', 'Shigella sonnei', 'Shigella sonnei', 'Shigella sonnei strain FDAARGOS_90, complete genome']
['70', 'gi|1348323427|gb|CP014099.2|', '7.05e-31', '150', '1348323427', 'CP014099', '624', 'Shigella sonnei', 'Shigella sonnei', 'Shigella sonnei strain FDAARGOS_90, complete genome']
['70', 'gi|1348323427|gb|CP014099.2|', '7.05e-31', '150', '1348323427', 'CP014099', '624', 'Shigella sonnei', 'Shigella sonnei', 'Shigella sonnei strain FDAARGOS_90, complete genome']
['70', 'gi|1348323427|gb|CP014099.2|', '7.05e-31', '150', '1348323427', 'CP014099', '624', 'Shigella sonnei', 'Shigella sonnei', 'Shigella sonnei strain FDAARGOS_90, complete genome']
['70', 'gi|1348323427|gb|CP014099.2|', '7.05e-31', '150', '1348323427', 'CP014099', '624', 'Shigella sonnei', 'Shigella sonnei', 'Shigella sonnei strain FDAARGOS_90, complete genome']
['70', 'gi|1348323427|gb|CP014099.2|', '7.05e-31', '150', '1348323427', 'CP01409

['70', 'gi|1347826600|gb|CP026784.1|', '0.0', '2231', '1347826600', 'CP026784', '622', 'Shigella dysenteriae', 'Shigella dysenteriae', 'Shigella dysenteriae strain 80-547 chromosome, complete genome']
['70', 'gi|1347826600|gb|CP026784.1|', '0.0', '2170', '1347826600', 'CP026784', '622', 'Shigella dysenteriae', 'Shigella dysenteriae', 'Shigella dysenteriae strain 80-547 chromosome, complete genome']
['70', 'gi|1347826600|gb|CP026784.1|', '0.0', '1206', '1347826600', 'CP026784', '622', 'Shigella dysenteriae', 'Shigella dysenteriae', 'Shigella dysenteriae strain 80-547 chromosome, complete genome']
['70', 'gi|1347826600|gb|CP026784.1|', '0.0', '1053', '1347826600', 'CP026784', '622', 'Shigella dysenteriae', 'Shigella dysenteriae', 'Shigella dysenteriae strain 80-547 chromosome, complete genome']
['70', 'gi|1347826600|gb|CP026784.1|', '6.43e-96', '366', '1347826600', 'CP026784', '622', 'Shigella dysenteriae', 'Shigella dysenteriae', 'Shigella dysenteriae strain 80-547 chromosome, complete 

['77', 'gi|1347826594|gb|CP026780.1|', '5.74e-90', '346', '1347826594', 'CP026780', '622', 'Shigella dysenteriae', 'Shigella dysenteriae', 'Shigella dysenteriae strain 53-3937 chromosome, complete genome']
['77', 'gi|1347826594|gb|CP026780.1|', '7.42e-89', '342', '1347826594', 'CP026780', '622', 'Shigella dysenteriae', 'Shigella dysenteriae', 'Shigella dysenteriae strain 53-3937 chromosome, complete genome']
['77', 'gi|1347826594|gb|CP026780.1|', '7.42e-89', '342', '1347826594', 'CP026780', '622', 'Shigella dysenteriae', 'Shigella dysenteriae', 'Shigella dysenteriae strain 53-3937 chromosome, complete genome']
['77', 'gi|1347826594|gb|CP026780.1|', '4.66e-56', '233', '1347826594', 'CP026780', '622', 'Shigella dysenteriae', 'Shigella dysenteriae', 'Shigella dysenteriae strain 53-3937 chromosome, complete genome']
['77', 'gi|1347826594|gb|CP026780.1|', '6.25e-30', '147', '1347826594', 'CP026780', '622', 'Shigella dysenteriae', 'Shigella dysenteriae', 'Shigella dysenteriae strain 53-3937 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [ ]:
from collections import Counter
count_names = Counter()
count_id = Counter()
total_length = 0
not_bacteria_node = []
unnown_id = []
with open(contera_log, "w") as fw:
    fw.write("UNNOWN ID'S: \n")
    for key, value in cont_to_blast.items():
        length = cont_to_len[key]
        val_split = value.split('.')[0]
        taxon_id = refids.find_one({"accession":val_split})
        print(taxon_id)
        if taxon_id == None:
            fw.write(key + " : " + val_split + "\n")
        else:
            taxon_id = taxon_id["taxid"]
            taxon_name = taxids.find_one({"_id":taxon_id})["name"]
            taxon_name = " ".join(taxon_name.split()[:2])
            count_names[taxon_name] += length
            count_id[taxon_id] += length
            total_length += length
            if taxon_name != count_names.most_common()[0][0]:
                not_bacteria_node.append(key)
                
print(not_bacteria_node)